In [20]:
from datetime import datetime, timezone
import pandas as pd
import requests
import json


PROXIES = {
    
   'http': 'http://discproxy.virtual.uniandes.edu.co:443',
}

EXCHANGE_ID = "402f5618-6a78-43ad-b4ee-44b3e65a94a7"




In [97]:
# Method to make a POST request to the specified API endpoint with a JSON payload
def post_method(url_path, data_dict):
    print("POST request to: " + url_path)
    # Convert the dictionary to a JSON string using the `json` module
    json_payload = json.dumps(data_dict)

    print(json_payload)
    # try:
    # Send the POST request with the JSON payload
    response = requests.post(url_path, data=json_payload, proxies=PROXIES)

    # Check if the request was successful
    if response.status_code == requests.codes.created:
        # If successful, print the response content and convert it to a Pandas DataFrame
        print("created post status code: " + str(response.status_code))

        print(response.content)
        json_data = json.loads(response.content)
        df = pd.json_normalize(json_data)
        return df
    else:
        # If unsuccessful, print the response content
        print("post status code: "+str(response.status_code))
        print(response.content)

def create_exchange(base_url, data_dict):
    # Call the `post_method` function with the appropriate URL and data dictionary
    print("Endpoint: " + base_url + "exchanges")
    resp = post_method(base_url + "exchanges", data_dict)
    return resp
# post_method(base_url + "exchanges", data_dict)
    
def create_asset(base_url,exchange_id, data_dict):
    # Call the `post_method` function with the appropriate URL and data dictionary
    print("Endpoint: " + base_url + "assets")
    resp = post_method(base_url + "exchanges/"+exchange_id+"/asset", data_dict)
    return resp
# post_method(base_url + "exchanges", data_dict)



In [98]:
base_url = "http://172.24.100.128:5000/"

dict =  {
    "symbol": "ETHUSDT",
    "base_asset": "ETH",
    "quote_asset": "USDT",
    "interval": "day",
    "asset_type": "Cryptocurrency"
  }


a = create_asset(base_url,EXCHANGE_ID,dict)



Endpoint: http://172.24.100.128:5000/assets
POST request to: http://172.24.100.128:5000/exchanges/402f5618-6a78-43ad-b4ee-44b3e65a94a7/asset
{"symbol": "ETHUSDT", "base_asset": "ETH", "quote_asset": "USDT", "interval": "day", "asset_type": "Cryptocurrency"}
post status code: 404
b'{"error message":"The Asset allready exists"}'


In [99]:
BTCUSDT_DAY_ID = "81d625dd-f73f-4829-a2ff-1d795fbc5b3a"
BTCUSDT_HOUR_ID = "7aa396ec-8c6a-44fd-89f2-12e7f998f883"
BTCUSDT_MINUTE_ID = "31deee63-e4bb-45ad-b020-8759b5c69e0f"


ETHUSDT_DAY_ID = "67da12e9-6fd9-4401-b16a-1c2dd589ff01"
ETHUSDT_HOUR_ID = "35515212-5467-45b4-b2e5-3ae048e482e7"
ETHUSDT_MINUTE_ID = "38d4f96b-26b7-420a-a34f-912f5ad23eaf"

In [100]:

from datetime import datetime, timezone
import pandas as pd
import requests
import json
import ta
import math
import yfinance as yf


BINANCE_URL = 'https://api.binance.com/api/v3/klines'

PROXIES = {    
   'http': 'http://discproxy.virtual.uniandes.edu.co:443',
}

# Method to make API request to retrieve the last recorded price timestamp for a given asset ID


def api_request_last_time_stamp_from_asset_id(base_url, asset_id):
    # try:
    print("entro api_request_last_time_stamp_from_asset_id")

    # Make GET request to API endpoint
    response = requests.get(base_url + "assets/" + asset_id + "/last_price/",proxies= PROXIES)

    # Check if the request was successful
    if response.status_code == requests.codes.ok:

        print("get las unix time status code: "+str(response.status_code))

        # Convert JSON response to Python dictionary
        json_data = json.loads(response.content)
        # Normalize the dictionary and convert it to a Pandas DataFrame
        df = pd.json_normalize(json_data)
        # Return the Unix timestamp of the last recorded price for the specified asset ID
        return int(df['unix_time'].iloc[0])
    else:
        print("fallo")
        print(response.content)
        json_data = json.loads(response.content)
        df = pd.json_normalize(json_data)
        return df
    # except:
    #     print("Failed api_request_last_time_stamp_from_asset_id")

# Method to make a GET request to the API endpoint


def api_request_get_asset_from_asset_id(base_url, exchange_id, asset_id):
    # try:
    # Make GET request to API endpoint

    response = requests.get(base_url + "exchanges/" +
                            exchange_id + "/asset/"+asset_id,proxies=PROXIES)

    # Check if the request was successful
    if response.status_code == requests.codes.ok:
        print("get asset status code: "+str(response.status_code))
        # Convert JSON response to Python dictionary
        json_data = json.loads(response.content)
        # Normalize the dictionary and convert it to a Pandas DataFrame
        df = pd.json_normalize(json_data)
        # Return the Unix timestamp of the last recorded price for the specified asset ID

        print("symbol: " + df["symbol"].iloc[0])
        print("interval: " + df["interval"].iloc[0])
        return df
    else:
        print(response.content)
        json_data = json.loads(response.content)
        df = pd.json_normalize(json_data)
        return df
    # except:
    #     print("Failed api_request_get_asset_from_asset_id")


# Method to make API request to retrieve prices for a given asset ID between two specified Unix timestamps
def api_request_get_prices_between_unix_time(base_url, asset_id, unix_time_start, unix_time_end):

    print("entro api_request_get_prices_between_unix_time")

    # try:
    # Make GET request to API endpoint with query parameters for start and end Unix timestamps
    response = requests.get(base_url + "assets/" + asset_id + "/indicators_unix_between/",
                            params={'unix_time_start': unix_time_start, 'unix_time_end': unix_time_end},proxies= PROXIES)

    print("status code time between: " + str(response.status_code))

    # Check if the request was successful
    if response.status_code == requests.codes.ok:
        print("get prices between status code: "+str(response.status_code))
        # Convert JSON response to Python dictionary
        json_data = json.loads(response.content)
        # Normalize the dictionary and convert it to a Pandas DataFrame
        df = pd.json_normalize(json_data)
        # Return the DataFrame containing the retrieved price data
        return df

    else:
        print("Failed api_request_get_prices_between_unix_time")
        json_data = json.loads(response.content)

        print(json_data)
        return json_data

    # except:
    #     print("Failed api_request_get_prices_between_unix_time")


# Method to make a POST request to the specified API endpoint with a JSON payload
def post_method(url_path, data_dict):
    # Convert the dictionary to a JSON string using the `json` module
    json_payload = json.dumps(data_dict)
    print("data : "+json_payload)


    # try:
    # Send the POST request with the JSON payload
    response = requests.post(url_path, data=json_payload,proxies= PROXIES)

    # Check if the request was successful
    if response.status_code == requests.codes.created:
        # If successful, print the response content and convert it to a Pandas DataFrame
        # print("post status code: " + str(response.status_code))

        # print(response.content)
        json_data = json.loads(response.content)
        df = pd.json_normalize(json_data)
        return df
    else:
        # If unsuccessful, print the response content
        print("post status code: "+str(response.status_code))
        print("failed: "+json_payload)
        print(response.content)

    # except:
    #     # If an exception occurs, print an error message
    #     print("Failed to make request")

# Method to create a new price for a given asset ID


def create_price_to_asset_id(base_url, asset_id, data_dict):
    # Call the `post_method` function with the appropriate URL and data dictionary
    return post_method(base_url + "assets/" + asset_id + "/prices/", data_dict)

# Method to create a new indicator for a given price ID


def create_indicator_to_price_id(base_url, price_id, data_dict):
    # Call the `post_method` function with the appropriate URL and data dictionary
    return post_method(base_url + "prices/" + price_id + "/indicators/", data_dict)


def round_minute(epoch_timestamp):
    # convert epoch timestamp to datetime object
    timestamp1 = datetime.utcfromtimestamp(epoch_timestamp)

    # round to nearest day
    rounded_timestamp1 = timestamp1.replace(
        second=0, microsecond=0, tzinfo=timezone.utc)

    # convert rounded timestamp back to epoch timestamp
    return int(rounded_timestamp1.timestamp())


def round_hour(epoch_timestamp):
    # convert epoch timestamp to datetime object
    timestamp2 = datetime.utcfromtimestamp(epoch_timestamp)

    # round to nearest hour
    rounded_timestamp2 = timestamp2.replace(
        minute=0, second=0, microsecond=0, tzinfo=timezone.utc)

    # convert rounded timestamp back to epoch timestamp
    return int(rounded_timestamp2.timestamp())


def round_day(epoch_timestamp):
    # convert epoch timestamp to datetime object
    timestamp3 = datetime.utcfromtimestamp(epoch_timestamp)

    # round to nearest day
    rounded_timestamp3 = timestamp3.replace(
        hour=0, minute=0, second=0, microsecond=0, tzinfo=timezone.utc)

    # convert rounded timestamp back to epoch timestamp
    return int(rounded_timestamp3.timestamp())


def get_data_from_api(
        symbol: str, interval: str, initial_timestamp: int, limit_timestamp: int):
    """ This function get the information from binance API
    """

    # Set working dates ------------------------------------------------------------------------------------
    # End of Looping Period Date
    # Load will go from initial_date to limit_date
    # Start date is inclusive

    # set fields
    fields = ['datetime', 'open', 'high', 'low', 'close', 'volume', 'close_time',
              'qav', 'num_trades', 'taker_base_vol', 'taker_quote_vol', 'ignore']

    counter = 0
    df_prices = pd.DataFrame(columns=fields)

    if interval == "minute":

        initial_timestamp = round_minute(initial_timestamp)
        limit_timestamp = round_minute(limit_timestamp)

        print("last time in the api: " +
              str(datetime.utcfromtimestamp(initial_timestamp)))
        print("Actual datetime: " + str(datetime.utcfromtimestamp(limit_timestamp)))

        if initial_timestamp + 60 < limit_timestamp:
            print("Si se trae data")
            initial_timestamp = initial_timestamp + 60
            limit_timestamp = limit_timestamp - 62
        else:
            print("Finalizo y no hay datos")
            return df_prices

        interval_binance = "1m"
        limit_binance = "960"
        following_period = 57600

        # We will work with time intervals of 16 hours when working with minutes to have 960 records per API call - LIMIT = 1000
        end_date_timestamp = initial_timestamp + following_period

    if interval == "hour":

        initial_timestamp = round_hour(initial_timestamp)
        limit_timestamp = round_hour(limit_timestamp)

        print("last time in the api: " +
              str(datetime.utcfromtimestamp(initial_timestamp)))
        print("Actual datetime: " + str(datetime.utcfromtimestamp(limit_timestamp)))

        if initial_timestamp + 3600 < limit_timestamp:
            print("Si se trae data")
            initial_timestamp = initial_timestamp + 3600
            limit_timestamp = limit_timestamp - 3602
        else:
            print("Finalizo y no hay datos")
            return df_prices

        interval_binance = "1h"
        limit_binance = "960"
        following_period = 144000

        # We will work with time intervals of 40 days when working with hours to have 960 records per API call - LIMIT = 1000
        end_date_timestamp = initial_timestamp + following_period

    if interval == "day":

        initial_timestamp = round_day(initial_timestamp)
        limit_timestamp = round_day(limit_timestamp)

        print("last time in the api: " +
              str(datetime.utcfromtimestamp(initial_timestamp)))
        print("Actual datetime: " + str(datetime.utcfromtimestamp(limit_timestamp)))

        if initial_timestamp + 86400 < limit_timestamp:
            print("Si se trae data")
            initial_timestamp = initial_timestamp + 86400
            limit_timestamp = limit_timestamp - 86402
        else:
            print("Finalizo y no hay datos")
            return df_prices

        interval_binance = "1d"
        limit_binance = "360"
        following_period = 31104000
        end_date_timestamp = initial_timestamp + following_period

    # Start time of function
    loop_start_time = datetime.now()

    # Loop through API calls ---------------------------------------------------------------------------
    while initial_timestamp < limit_timestamp:
        print("Entro loop")

        # Set dates to Binance API format
        start = str(initial_timestamp*1000)

        if end_date_timestamp > limit_timestamp:
            end = str(limit_timestamp*1000)
        else:
            end = str(end_date_timestamp*1000)

        par = {'symbol': symbol, 'interval': interval_binance,
               'startTime': start, 'endTime': end, 'limit': limit_binance}

        # API CALL
        response = requests.get(BINANCE_URL, params=par)
        json_data = json.loads(response.content)
        new_df = pd.DataFrame(json_data, columns=fields)
        df_prices = pd.concat([df_prices, new_df], axis=0)

        # Move to following period
        initial_timestamp = end_date_timestamp
        end_date_timestamp = initial_timestamp + following_period
        counter += 1

    # End time of function
    loop_end_time = datetime.now()

    time = loop_end_time - loop_start_time

    print('DONE', '\nDURATION:', time.days, 'DAYS', time.seconds//3600, 'HOURS',
          (time.seconds//60) % 60, 'MINUTES', time.seconds % 60, 'SECONDS.')
    print('API CALLS:', counter, ' ROWS:', len(df_prices))

    df_prices = df_prices.rename(columns={'datetime': 'unix_time',
                                          'open': 'open_price',
                                          'high': 'high_price',
                                          'low': 'low_price',
                                          'close': 'close_price'})

    df_prices['unix_time'] = df_prices['unix_time'].apply(
        lambda x: int(round(x / 1000)))

    return df_prices


def get_last_timestamp(base_url, asset_id, interval):

    last_timestamp_response = api_request_last_time_stamp_from_asset_id(
        base_url, asset_id)

    last_timestamp = None
    first_report = None

    if isinstance(last_timestamp_response, int):
        first_report = False
        last_timestamp = last_timestamp_response
    else:
        if last_timestamp_response["error message"].iloc[0] == "There are not prices for this asset":
            print("There are not prices for this asset")

            first_report = True

            if interval == "minute":
                last_timestamp = 1638230400  # 30 of november 2021
            if interval == "hour":
                last_timestamp = 1638230400  # 30 of november 2021
            if interval == "day":
                last_timestamp = 1630368000  # 31 of august 2021

        elif last_timestamp_response["error message"].iloc[0] == "The Asset with the given id was not found":
            print("The Asset with the given id was not found")
            last_timestamp = None

    return last_timestamp, first_report


# method to add the thecnic indicators to the dataframe
def add_indicators(df):

    # momentum
    df['ao'] = ta.momentum.awesome_oscillator(
        high=df['high_price'], low=df['low_price'])
    df['kama'] = ta.momentum.kama(close=df['close_price'])
    df['ppo'] = ta.momentum.ppo(close=df['close_price'])
    df['pvo'] = ta.momentum.pvo(volume=df['volume'])
    df['roc'] = ta.momentum.roc(close=df['close_price'])
    df['rsi'] = ta.momentum.rsi(close=df['close_price'])
    df['stochrsi'] = ta.momentum.stochrsi(close=df['close_price'])
    df['stoch'] = ta.momentum.stoch(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])
    df['tsi'] = ta.momentum.tsi(close=df['close_price'])
    df['uo'] = ta.momentum.ultimate_oscillator(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])
    df['wri'] = ta.momentum.williams_r(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])

    # volume
    df['accdist'] = ta.volume.acc_dist_index(
        high=df['high_price'], low=df['low_price'], close=df['close_price'], volume=df['volume'])
    df['cmf'] = ta.volume.chaikin_money_flow(
        high=df['high_price'], low=df['low_price'], close=df['close_price'], volume=df['volume'])
    df['emv'] = ta.volume.ease_of_movement(
        high=df['high_price'], low=df['low_price'], volume=df['volume'])
    df['fi'] = ta.volume.force_index(
        close=df['close_price'], volume=df['volume'])
    df['mfi'] = ta.volume.money_flow_index(
        high=df['high_price'], low=df['low_price'], close=df['close_price'], volume=df['volume'])
    df['nvi'] = ta.volume.negative_volume_index(
        close=df['close_price'], volume=df['volume'])
    df['obv'] = ta.volume.on_balance_volume(
        close=df['close_price'], volume=df['volume'])
    df['smaemv'] = ta.volume.sma_ease_of_movement(
        high=df['high_price'], low=df['low_price'], volume=df['volume'])
    df['vpt'] = ta.volume.volume_price_trend(
        close=df['close_price'], volume=df['volume'])
    df['vwap'] = ta.volume.volume_weighted_average_price(
        high=df['high_price'], low=df['low_price'], close=df['close_price'], volume=df['volume'])

    # volatility
    df['atr'] = ta.volatility.average_true_range(
        high=df['high_price'], low=df['low_price'], close=df['close_price'])
    df['ulcer'] = ta.volatility.ulcer_index(close=df['close_price'])

    df['bbh'] = ta.volatility.bollinger_hband(close=df['close_price'])
    df['bbl'] = ta.volatility.bollinger_lband(close=df['close_price'])
    df['bbhi'] = ta.volatility.bollinger_hband_indicator(
        close=df['close_price'])
    df['bbli'] = ta.volatility.bollinger_lband_indicator(
        close=df['close_price'])
    df['bbmavg'] = ta.volatility.bollinger_mavg(close=df['close_price'])
    df['bb_pb'] = ta.volatility.bollinger_pband(close=df['close_price'])
    df['bb_wb'] = ta.volatility.bollinger_wband(close=df['close_price'])

    df['dchb'] = ta.volatility.donchian_channel_hband(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])
    df['dclb'] = ta.volatility.donchian_channel_lband(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])
    df['dcmb'] = ta.volatility.donchian_channel_mband(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])
    df['dcpb'] = ta.volatility.donchian_channel_pband(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])
    df['dcwb'] = ta.volatility.donchian_channel_wband(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])

    df['kchb'] = ta.volatility.keltner_channel_hband(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])
    df['kclb'] = ta.volatility.keltner_channel_lband(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])
    df['kchbi'] = ta.volatility.keltner_channel_hband_indicator(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])
    df['kclbi'] = ta.volatility.keltner_channel_lband_indicator(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])
    df['kcmb'] = ta.volatility.keltner_channel_mband(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])
    df['kcpb'] = ta.volatility.keltner_channel_pband(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])
    df['kcwb'] = ta.volatility.keltner_channel_wband(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])

    # trend

    # En dos de estos tres hay algo que esta botando warning
    df['adx'] = ta.trend.adx(close=df['close_price'],
                             high=df['high_price'], low=df['low_price'])
    df['adx_neg'] = ta.trend.adx_neg(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])
    df['adx_pos'] = ta.trend.adx_pos(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])

    df['aroon_up'] = ta.trend.aroon_up(close=df['close_price'])
    df['aroon_down'] = ta.trend.aroon_down(close=df['close_price'])

    df['cci'] = ta.trend.cci(close=df['close_price'],
                             high=df['high_price'], low=df['low_price'])
    df['dpo'] = ta.trend.dpo(close=df['close_price'])
    df['kst'] = ta.trend.kst(close=df['close_price'])
    df['kst_sig'] = ta.trend.kst_sig(close=df['close_price'])
    df['ema'] = ta.trend.ema_indicator(close=df['close_price'])

    df['ichimoku_a'] = ta.trend.ichimoku_a(
        high=df['high_price'], low=df['low_price'])
    df['ichimoku_b'] = ta.trend.ichimoku_b(
        high=df['high_price'], low=df['low_price'])
    df['ichimoku_base_line'] = ta.trend.ichimoku_base_line(
        high=df['high_price'], low=df['low_price'])
    df['ichimoku_conversion_line'] = ta.trend.ichimoku_conversion_line(
        high=df['high_price'], low=df['low_price'])

    df['macd'] = ta.trend.macd(close=df['close_price'])
    df['macd_diff'] = ta.trend.macd_diff(close=df['close_price'])
    df['macd_signal'] = ta.trend.macd_signal(close=df['close_price'])

    df['mi'] = ta.trend.mass_index(high=df['high_price'], low=df['low_price'])
    df['sma'] = ta.trend.sma_indicator(close=df['close_price'])
    df['wma'] = ta.trend.wma_indicator(close=df['close_price'])
    df['stc'] = ta.trend.stc(close=df['close_price'])
    df['trix'] = ta.trend.trix(close=df['close_price'])

    # df['psar_down'] = ta.trend.psar_down(close=df['close_price'],high=df['high_price'],low=df['low_price'])
    # df['psar_up'] = ta.trend.psar_up(close=df['close_price'],high=df['high_price'],low=df['low_price'])
    # df['psar_down_indicator'] = ta.trend.psar_down_indicator(
    #     close=df['close_price'], high=df['high_price'], low=df['low_price'])
    # df['psar_up_indicator'] = ta.trend.psar_up_indicator(
    #     close=df['close_price'], high=df['high_price'], low=df['low_price'])

    df['vi_pos'] = ta.trend.vortex_indicator_pos(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])
    df['vi_neg'] = ta.trend.vortex_indicator_neg(
        close=df['close_price'], high=df['high_price'], low=df['low_price'])

    return df


def upload_prices(df_prices, base_url, asset_id):

    if df_prices.empty:
        print("There are NO prices to upload")
    else:
        print("There are prices to upload")
        # loop through all rows and convert each row to a JSON object
        for index, row in df_prices.iterrows():

            row_dict = row.to_dict()
            resp = create_price_to_asset_id(base_url, asset_id, row_dict)

    print("DONE upload_prices")


# Define a function to convert Unix timestamp to date string
# def unix_to_date(unix_timestamp):
#     datetime_obj = datetime.utcfromtimestamp(unix_timestamp)
#     date_str = datetime_obj.date().strftime('%Y-%m-%d')
#     return date_str


# Method to get
def get_full_prices_past(base_url, asset_id, interval, last_timestamp, first_report, final_timestamp):


    if first_report:
        print("first report")
        first_indicator_time = last_timestamp
        timestamp_to_add = last_timestamp

    else:
        if interval == "minute":
            first_indicator_time = last_timestamp - 6000
            timestamp_to_add = last_timestamp - 60

        if interval == "hour":
            first_indicator_time = last_timestamp - 360000
            timestamp_to_add = last_timestamp - 3600
        if interval == "day":
            first_indicator_time = last_timestamp - 8640000
            timestamp_to_add = last_timestamp - 86400

    df_prices = api_request_get_prices_between_unix_time(
        base_url, asset_id, first_indicator_time, final_timestamp)

    df_prices_wit_indicators = add_indicators(df_prices)

    df_prices_wit_indicators.drop(['low_price', 'asset_id', 'updated_at', 'high_price', 'volume', 'date_time_utc', 'qav', 'date_time_gmt_5',
                                  'num_trades', 'open_price', 'taker_base_vol', 'close_price', 'taker_quote_vol', 'created_at', 'ignore'], axis=1, inplace=True)

    df_prices_wit_indicators = df_prices_wit_indicators.loc[
        df_prices_wit_indicators['unix_time'] >= timestamp_to_add]

    # Apply the function to the 'unix_timestamp' column and create a new column called 'date'
    df_prices_wit_indicators['timestamp_round_day'] = df_prices_wit_indicators['unix_time'].apply(
        round_day)

    return df_prices_wit_indicators


# Method to post the indicators to the API
def upload_indicators(df_with_indicators, base_url):

    # loop through all rows and convert each row to a JSON object

    for index, row in df_with_indicators.iterrows():

        row_dict = row.to_dict()
        price_id = row_dict["id"]
        unix_time = row_dict["unix_time"]
        del row_dict['unix_time']
        del row_dict['id']
        # Iterate over the dictionary
        for key, value in row_dict.items():
            if math.isnan(value):
                data_dict = {
                    "name": key,
                    "unix_time": unix_time
                }
            else:
                data_dict = {
                    "name": key,
                    "value": value,
                    "unix_time": unix_time
                }

            print("upload", data_dict)
            print("price_id", price_id)
            
            create_indicator_to_price_id(base_url, price_id, data_dict)


def get_extra_assets_data(start_date, end_date, name, ticker):

    print("Getting data for: " + name + " "+ticker)

    df = yf.Ticker(ticker).history(
        interval="1d", start=start_date, end=end_date)
    df = df.reset_index(drop=False)

    # df['date']= df['Date'].dt.date

    df['unix_time'] = df['Date'].dt.date.apply(
        lambda x: int(pd.Timestamp(x).timestamp()))

    # Apply the function to the 'unix_timestamp' column and create a new column called 'date'
    df['timestamp_round_day'] = df['unix_time'].apply(round_day)

    df.drop(['Open', 'High', 'Low', 'Volume', 'Dividends',
            'Stock Splits', 'Date','unix_time'], axis=1, inplace=True)


    df.rename(columns={'Close': name}, inplace=True)

    print("DONE getting data for" + name + " "+ticker)
    return df


def create_df_extra_assets_data(start_date, end_date):

    dict_assets_extra = {
        "gold": "GC=F",
        "silver ": "SI=F",
        "NaturalGas": "NG=F",
        "cotton ": "CT=F",
        "coffee ": "KC=F",
        "sugar ": "SB=F",
        "cocoa ": "CC=F",
        "rice ": "ZR=F",
        "corn ": "ZC=F",
        "vwheat ": "KE=F",
        "soybean ": "ZS=F",
        "cotton ": "CT=F",
        "oat ": "ZO=F",
        "spy500 ": "ES=F",
        "dowJones ": "YM=F",
        "nasdaq ": "NQ=F",
        "Russell2000 ": "RTY=F",
        "usBond10y ": "ZN=F",
        "usBond5y ": "ZF=F",
        "usBond2y ": "ZT=F",
        "usBond ": "ZB=F"
    }


    df_extra_assets_data = pd.DataFrame()
    count = 0

    for key, value in dict_assets_extra.items():

        if count == 0:
            df_extra_assets_data = get_extra_assets_data(
                start_date, end_date, name=key, ticker=value)

        else:
            df_extra_assets_data = pd.merge(df_extra_assets_data, get_extra_assets_data(
                start_date, end_date, name=key, ticker=value), on='timestamp_round_day', how='outer')

        count += 1
    
    return df_extra_assets_data


In [95]:
from datetime import datetime
# from utils import *
import os

pd.set_option('display.max_columns', 100)


EXCHANGE_ID = "402f5618-6a78-43ad-b4ee-44b3e65a94a7"
BTCUSDT_HOUR_ID = "7aa396ec-8c6a-44fd-89f2-12e7f998f883"


In [101]:
base_url = "http://172.24.100.128:5000/"
ASSET_ID = BTCUSDT_HOUR_ID

final_timestamp = int(datetime.now().timestamp())


# Get the asset from the API
asset = api_request_get_asset_from_asset_id(base_url,EXCHANGE_ID,ASSET_ID)


# Get the last recorded price timestamp for the specified asset ID
last_timestamp , first_report  = get_last_timestamp(base_url,ASSET_ID,asset["interval"].iloc[0])

# Get the prices from the BINANCE API
df_prices_final = get_data_from_api(symbol=asset["symbol"].iloc[0], interval=asset["interval"].iloc[0], initial_timestamp=last_timestamp, limit_timestamp=final_timestamp)

# Upload the prices to the API
upload_prices(df_prices_final,base_url,ASSET_ID)

df_with_indicators = get_full_prices_past( base_url, ASSET_ID, asset["interval"].iloc[0], last_timestamp, first_report,final_timestamp)

df_extra_assets_data = create_df_extra_assets_data(start_date=last_timestamp, end_date=final_timestamp)

df_final = pd.merge(df_with_indicators, df_extra_assets_data , on='timestamp_round_day', how='left')

df_final.drop(['timestamp_round_day'], axis=1, inplace=True)


upload_indicators(df_final,base_url)

get asset status code: 200
symbol: BTCUSDT
interval: hour
entro api_request_last_time_stamp_from_asset_id
fallo
b'{"error message":"There are not prices for this asset"}'
There are not prices for this asset
last time in the api: 2021-11-30 00:00:00
Actual datetime: 2023-04-12 05:00:00
Si se trae data
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro loop
Entro

/Users/julianoliverosforero/Desktop/2023-1/Tesis/cryptocurrency-market-prediction-project/data-loader/env/lib/python3.9/site-packages/ta/trend.py:780: RuntimeWarning: invalid value encountered in scalar divide
  dip[idx] = 100 * (self._dip[idx] / value)
/Users/julianoliverosforero/Desktop/2023-1/Tesis/cryptocurrency-market-prediction-project/data-loader/env/lib/python3.9/site-packages/ta/trend.py:785: RuntimeWarning: invalid value encountered in scalar divide
  din[idx] = 100 * (self._din[idx] / value)


In [87]:
df_with_indicators

id   unix_time           ao  \
99   048b76cc-8047-4832-bb75-06efe57ad778  1681084800  1795.179412   
100  2775ff08-68f8-4a0c-b686-af1f2c05838a  1681171200  1980.565588   

             kama       ppo        pvo       roc        rsi  stochrsi  \
99   27415.797635  3.148443 -51.926732  4.546045  68.818637       1.0   
100  27773.549908  3.467225 -49.753610  7.748854  71.402025       1.0   

         stoch        tsi         uo        wri       accdist       cmf  \
99   95.772763  24.400389  62.474116  -4.227237  2.427884e+06  0.052511   
100  89.564028  27.135856  62.555652 -10.435972  2.446358e+06  0.149764   

              emv            fi        mfi          nvi           obv  \
99   1.900993e+09  2.451623e+07  57.489792  1054.175645  808463.29289   
100  1.553168e+09  2.648304e+07  66.998360  1054.175645  876453.36910   

           smaemv          vpt          vwap          atr     ulcer  \
99   2.670512e+08  3590.984120  28125.473928  1024.547847  1.539540   
100  3.933365e+08  4433.995495  28399.564484  1019.937286  1.189833   

              bbh           bbl  bbhi  bbli      bbmavg     bb_pb     bb_wb  \
99   29109.621743  26916.381257   1.0   0.0  28013.0015  1.240611  7.829366   
100  29559.189461  26761.758539   1.0   0.0  28160.4740  1.229221  9.933891   

        dchb      dclb      dcmb      dcpb       dcwb          kchb  \
99   29770.0  26508.14  28485.12  0.948377   9.093286  29028.427500   
100  30550.0  26508.14  28875.12  0.895640  11.780519  29090.108333   

             kclb  kchbi  kclbi          kcmb      kcpb      kcwb        adx  \
99   26937.795500    1.0    0.0  27983.111500  1.291258  7.471049  32.110367   
100  27130.101333    1.0    0.0  28110.104833  1.566484  6.972607  33.409005   

       adx_neg    adx_pos  aroon_up  aroon_down         cci       dpo  \
99   11.855944  29.989767     100.0         8.0  248.407338   15.5285   
100  11.058892  33.435894     100.0         4.0  326.731329  304.8860   

            kst     kst_sig           ema  ichimoku_a  ichimoku_b  \
99   142.042518  168.285720  28215.932571    27715.81   24659.545   
100  143.529554  162.309869  28521.238329    28297.56   25049.545   

     ichimoku_base_line  ichimoku_conversion_line        macd  macd_diff  \
99              26946.5                  28485.12  861.246599 -73.987198   
100             27720.0                  28875.12  955.757244  16.418758   

     macd_signal         mi           sma           wma        stc      trix  \
99    935.233797  23.697985  28257.800000  28387.782222   6.503345  0.545241   
100   939.338486  23.396283  28438.790833  28780.155556  23.862666  0.539387   

       vi_pos    vi_neg  timestamp_round_day  
99   1.130884  0.862478           1681084800  
100  1.231673  0.762706           1681171200

In [88]:
df_extra_assets_data

gold  timestamp_round_day    silver   NaturalGas    cotton   \
0  2004.800049           1681171200  25.131001       2.186  82.750000   
1  2035.800049           1681257600  25.545000       2.213  82.599998   

      coffee      sugar   cocoa   rice   corn   vwheat   soybean     oat   \
0  187.350006  23.700001  2893.0  17.24  651.0   868.25   1497.25  340.25   
1         NaN        NaN     NaN    NaN  625.5   867.00   1466.25  336.75   

   spy500   dowJones    nasdaq   Russell2000   usBond10y    usBond5y   \
0  4136.50    33852.0  13074.75   1798.300049  115.375000  109.765625   
1  4138.25    33877.0  13076.50   1798.300049  115.390625  109.812500   

    usBond2y     usBond   
0  103.238281  132.37500  
1  103.257812  132.28125

In [89]:
df_final


id   unix_time           ao  \
0  048b76cc-8047-4832-bb75-06efe57ad778  1681084800  1795.179412   
1  2775ff08-68f8-4a0c-b686-af1f2c05838a  1681171200  1980.565588   

           kama       ppo        pvo       roc        rsi  stochrsi  \
0  27415.797635  3.148443 -51.926732  4.546045  68.818637       1.0   
1  27773.549908  3.467225 -49.753610  7.748854  71.402025       1.0   

       stoch        tsi         uo        wri       accdist       cmf  \
0  95.772763  24.400389  62.474116  -4.227237  2.427884e+06  0.052511   
1  89.564028  27.135856  62.555652 -10.435972  2.446358e+06  0.149764   

            emv            fi        mfi          nvi           obv  \
0  1.900993e+09  2.451623e+07  57.489792  1054.175645  808463.29289   
1  1.553168e+09  2.648304e+07  66.998360  1054.175645  876453.36910   

         smaemv          vpt          vwap          atr     ulcer  \
0  2.670512e+08  3590.984120  28125.473928  1024.547847  1.539540   
1  3.933365e+08  4433.995495  28399.564484  1019.937286  1.189833   

            bbh           bbl  bbhi  bbli      bbmavg     bb_pb     bb_wb  \
0  29109.621743  26916.381257   1.0   0.0  28013.0015  1.240611  7.829366   
1  29559.189461  26761.758539   1.0   0.0  28160.4740  1.229221  9.933891   

      dchb      dclb      dcmb      dcpb       dcwb          kchb  \
0  29770.0  26508.14  28485.12  0.948377   9.093286  29028.427500   
1  30550.0  26508.14  28875.12  0.895640  11.780519  29090.108333   

           kclb  kchbi  kclbi          kcmb      kcpb      kcwb        adx  \
0  26937.795500    1.0    0.0  27983.111500  1.291258  7.471049  32.110367   
1  27130.101333    1.0    0.0  28110.104833  1.566484  6.972607  33.409005   

     adx_neg    adx_pos  aroon_up  aroon_down         cci       dpo  \
0  11.855944  29.989767     100.0         8.0  248.407338   15.5285   
1  11.058892  33.435894     100.0         4.0  326.731329  304.8860   

          kst     kst_sig           ema  ichimoku_a  ichimoku_b  \
0  142.042518  168.285720  28215.932571    27715.81   24659.545   
1  143.529554  162.309869  28521.238329    28297.56   25049.545   

   ichimoku_base_line  ichimoku_conversion_line        macd  macd_diff  \
0             26946.5                  28485.12  861.246599 -73.987198   
1             27720.0                  28875.12  955.757244  16.418758   

   macd_signal         mi           sma           wma        stc      trix  \
0   935.233797  23.697985  28257.800000  28387.782222   6.503345  0.545241   
1   939.338486  23.396283  28438.790833  28780.155556  23.862666  0.539387   

     vi_pos    vi_neg         gold    silver   NaturalGas  cotton   \
0  1.130884  0.862478          NaN        NaN         NaN      NaN   
1  1.231673  0.762706  2004.800049  25.131001       2.186    82.75   

      coffee      sugar   cocoa   rice   corn   vwheat   soybean     oat   \
0         NaN        NaN     NaN    NaN    NaN      NaN       NaN     NaN   
1  187.350006  23.700001  2893.0  17.24  651.0   868.25   1497.25  340.25   

   spy500   dowJones    nasdaq   Russell2000   usBond10y    usBond5y   \
0      NaN        NaN       NaN           NaN         NaN         NaN   
1   4136.5    33852.0  13074.75   1798.300049     115.375  109.765625   

    usBond2y   usBond   
0         NaN      NaN  
1  103.238281  132.375